In [12]:
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.cm as cmx
from matplotlib import colors
from matplotlib import lines
from pathlib import Path
import matplotlib.font_manager as fm 
from matplotlib.patches import Patch

In [13]:
# Set environment options
gpd.options.io_engine = "pyogrio"

In [14]:
# Load the "Jost" font needed for this plot
font_dir = ['./source/Jost_Font/']  # Font is located in Jost_Font folder
for font in fm.findSystemFonts(font_dir):
    fm.fontManager.addfont(font)

In [15]:
# Load datasets needed for this plot

# Voter participation data
data = pd.read_csv("./source/NRW2023-wahlbeteiligung.csv", sep=';')

# Swiss map boundaries data
border_folder = Path("./source/boundaries")
map_canton = gpd.read_file(str(border_folder / "k4k23.shx"))
map_municipality = gpd.read_file(str(border_folder / "k4g23.shx"))

In [16]:
# Adjust data to needs of this plot

# Only use voter data of municipalities
data_municipality = data[data["ebene_resultat"].isin(["Gemeinde"])]
# Add a column with canton abbreviations for annotations
data_municipality["kanton_abbr"] = data_municipality["kanton_nummer"].map({1: "ZH", 2: "BE", 3: "LU", 4: "UR", 5: "SZ", 6: "OW", 7: "NW", 8: "GL", 9: "ZG", 10: "FR", 11: "SO", 12: "BS", 13: "BL", 14: "SH", 15: "AR", 16: "AI", 17: "SG", 18: "GR", 19: "AG", 20: "TG", 21: "TI", 22: "VD", 23: "VS", 24: "NE", 25: "GE", 26: "JU",})
# Rename the municipality name column
map_municipality = map_municipality.rename(columns={'GMDNAME': 'gemeinde_bezeichnung'})
# Merge the voter data and the map border data
map_municipality = map_municipality.merge(data_municipality, on="gemeinde_bezeichnung")
# Add a column with the density of voters in voters per square kilometer
map_municipality["voter_per_qkm2"] = map_municipality["wahlberechtigte"].astype(int) / (map_municipality["AREA_HA"].astype(float) / 100)

C:\Users\z00433wm\AppData\Local\Temp\ipykernel_5508\305196385.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_municipality["kanton_abbr"] = data_municipality["kanton_nummer"].map({1: "ZH", 2: "BE", 3: "LU", 4: "UR", 5: "SZ", 6: "OW", 7: "NW", 8: "GL", 9: "ZG", 10: "FR", 11: "SO", 12: "BS", 13: "BL", 14: "SH", 15: "AR", 16: "AI", 17: "SG", 18: "GR", 19: "AG", 20: "TG", 21: "TI", 22: "VD", 23: "VS", 24: "NE", 25: "GE", 26: "JU",})


In [17]:
cmap = colors.LinearSegmentedColormap.from_list(name="my_cmap", 
                                                colors=[(0, "white"), (0.04336, "cornflowerblue"), (1, "crimson")])

In [18]:
cmap_colorbar = cmx.ScalarMappable(cmap=cmap)

In [19]:
# Define elements used for the legend
legend_elements = [
       Patch(edgecolor='black', facecolor='white', label='0 voters/km²'),
       Patch(facecolor='cornflowerblue', label='216.8 voters/km² (Swiss average)'),
       Patch(facecolor='crimson', label='>5000 voters/km²'),
]

# Define look and feel of legend
legend_kwargs = {
       'prop': {'family': 'Jost', 'size': 24, 'weight': 'regular'}, 
       'labelcolor': 'dimgrey', 
       'framealpha': 0, 
       'labelspacing': 0.2, 
       'handlelength': 2, 
       'handleheight': 1.25, 
       'handletextpad': 0.6,
}

In [20]:
# Prepare annotation items -> most, least and average densely populated municipality
sorted_by_density = map_municipality.sort_values('voter_per_qkm2')

highest = sorted_by_density.tail(1)
lowest = sorted_by_density.head(1)
differences = (sorted_by_density['voter_per_qkm2'] - 216.8).abs() 
average = sorted_by_density.loc[[differences.idxmin()]]

annotation_items = {
    f'{highest["gemeinde_bezeichnung"].values[0]}, {highest["kanton_abbr"].values[0]}': [highest, (0.05, 0.5), {'connectionstyle': "arc3,rad=0.2"}],
    f'{lowest["gemeinde_bezeichnung"].values[0]}, {lowest["kanton_abbr"].values[0]}': [lowest, (0.54, 0.075), {'connectionstyle': "arc3,rad=-0.2"}],
    f'{average["gemeinde_bezeichnung"].values[0]}, {average["kanton_abbr"].values[0]}': [average, (0.85, 0.9), {'connectionstyle': "arc3,rad=-0.2"}]
}

# Define ellipse items used for map highlighting
ellipse_items = [
    ((0.45, 0.55), 0.1, 0.2, 0), # Lucerne
    ((0.6125, 0.5875), 0.1, 0.11, 20), # Schwyz
    ((0.575, 0.9125), 0.1, 0.11, 0), # Schaffhausen
    ((0.45, 0.25), 0.15, 0.35, -25) # Wallis
]

# Define look and feel of annotation arrows
arrowprops = {
       'arrowstyle': 'Simple',
       'edgecolor': 'white',
       'facecolor': 'black',
       'linewidth': 1.5,
}

In [21]:
from matplotlib.patches import Ellipse

def do_annotations(axis):
    # Draw highlighting ellipses
    ellipses = []
    for xy, size_x, size_y, rotation, in ellipse_items:
        ellipses.append(Ellipse(xy, size_x, size_y, angle=rotation, alpha=1, ec='gold', linewidth=5, fill=False, transform=axis.transAxes))
        ellipses.append(Ellipse(xy, size_x, size_y, angle=rotation, alpha=0.05, fc='gold', fill=True, transform=axis.transAxes))
    
    for ellipse in ellipses:
        axis.add_artist(ellipse)

    # Draw annotation items
    for key, item in annotation_items.items():
        axis.annotate(
            key,
            xy=(item[0]['geometry'].centroid.x, item[0]['geometry'].centroid.y), xycoords='data',
            xytext=item[1], textcoords='axes fraction',
            size=30, va="center", ha="center",
            arrowprops={**item[2], **arrowprops},
            fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'}
        )
        
        text_x = item[1][0]
        text_y = item[1][1]
        text_y = text_y + 0.025 if text_y >= 0.5 else text_y - 0.025
        axis.text(text_x, text_y, f"{item[0]['voter_per_qkm2'].values[0]:.1f} voters/km²", fontproperties={'family': 'Jost', 'size': 20, 'weight': 'regular'}, 
                  horizontalalignment='center', verticalalignment='center', transform=axis.transAxes)

In [22]:
# Create figure and axis
f, ax = plt.subplots(figsize=(36, 27), dpi=300)
p = map_municipality.plot(column="voter_per_qkm2", ax=ax, linewidth=1, edgecolor='white', cmap=cmap, vmax=5000)
map_canton.plot(ax=ax, linewidth=3.5, edgecolor='black', color=(0, 0, 0, 0)) # Thicker canton borders

# Disable all ticks
ax.tick_params(which='both', bottom=False, top=False, right=False, left=False, labelleft=False, labelbottom=False) 

# Disable all spines
ax.spines.bottom.set_visible(False)
ax.spines.top.set_visible(False)
ax.spines.left.set_visible(False)
ax.spines.right.set_visible(False)

# Draw annotations
do_annotations(ax)

# Draw the legend
cbaxes = cbaxes = f.add_axes([0.157, 0.65, 0.02, 0.18]) 
cbar = plt.colorbar(cmap_colorbar, cax=cbaxes, orientation='vertical')
cbar.set_ticks([0, 0.04336, 1], labels=['', '', ''])

f.add_artist(lines.Line2D([0.155, 0.195], [0.83, 0.83], color='crimson', linewidth=5))
f.add_artist(lines.Line2D([0.155, 0.185], [0.6585, 0.6585], color='cornflowerblue', linewidth=5))
f.add_artist(lines.Line2D([0.185, 0.185], [0.6585, 0.749], color='cornflowerblue', linewidth=5))
f.add_artist(lines.Line2D([0.185, 0.195], [0.749, 0.749], color='cornflowerblue', linewidth=5))
f.add_artist(lines.Line2D([0.155, 0.195], [0.649, 0.649], color='black', linewidth=5))
f.text(x=0.2, y=0.645, s='0 voters/km²', color='dimgrey', fontproperties={'family': 'Jost', 'size': 24, 'weight': 'regular'})
f.text(x=0.2, y=0.745, s='216.8 voters/km² (Swiss average)', color='dimgrey', fontproperties={'family': 'Jost', 'size': 24, 'weight': 'regular'})
f.text(x=0.2, y=0.825, s='>5000 voters/km²', color='dimgrey', fontproperties={'family': 'Jost', 'size': 24, 'weight': 'regular'})

# Set title
f.suptitle('Voter Population Density on Municipality Level', fontproperties={'family': 'Jost', 'size': 60, 'weight': 'bold'}, x=0.405, y=0.9)

# Set subtitle
f.text(x=0.157, y=0.85, s=f"The density of voters per municipality in voters/km²", color='dimgrey', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'regular'})

# Set sources
f.text(x=0.8, y=0.175, s="Sources: bfs.admin.ch", color='dimgrey', fontproperties={'family': 'Jost', 'size': 18, 'weight': 'semibold'})

# Save the figure
plt.savefig('build/population_density_municipality.png', bbox_inches='tight', pad_inches=0.5)

d:\private_git\data-visualizations\venv\lib\site-packages\matplotlib\text.py:1461: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  x = float(self.convert_xunits(x))
d:\private_git\data-visualizations\venv\lib\site-packages\matplotlib\text.py:1463: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  y = float(self.convert_yunits(y))
